In [ ]:
import numpy as np
import plotly.express as px
def plot_embedding(embedding, labels=None):
    """
    Plot a 2D embedding with optional labels for coloring.

    Args:
        embedding (ndarray): shape (n_samples, 2)
        labels (array-like, optional): labels for coloring points
    """
    if labels is None:
        labels = np.zeros(embedding.shape[0])  # default: all same

    fig = px.scatter(
        x=embedding[:, 0],
        y=embedding[:, 1],
        color=labels.astype(str),  # convert to string for discrete legend
        title="2D Embedding Visualization",
        labels={"x": "Dim 1", "y": "Dim 2", "color": "Label"}
    )

    fig.update_layout(
        width=1000,
        height=800,
        title="Custom size Plotly figure"
    )


    fig.show()

In [18]:
f_path='/Users/chandrasekharmukherjee/Data/scRNA_IBD/'
d_path=['bcells_final.h5ad',
'cd4tcells_final.h5ad',
'cd8tcells_final.h5ad',
'epicolonic_final.h5ad',
'fibperi_final.h5ad',
'ilc_final.h5ad',
'ilealepi_final.h5ad',
'myeloid_final.h5ad',
'plasmacells_final.h5ad']

subset_number=1

import scanpy as sc
adata=sc.read_h5ad(f_path+d_path[subset_number])
X=adata.obsm['X_harmony']
n=X.shape[0]
print(n)
label=adata.obs['final_analysis'].to_numpy()
pt_label=adata.obs['Patient'].to_numpy()


145704


In [ ]:
import scanpy as sc
nk_path='/Users/chandrasekharmukherjee/PycharmProjects/Personal/cplearn_biotest/NK_cells.h5ad'
adata = sc.read_h5ad(nk_path)
X=adata.obsm['X_HARMONY']
label=adata.obs['ident'].to_numpy()

In [ ]:
import data_call
import numpy as np
d_name='Muraro'
X,label=data_call.get_dataset(d_name, mode='PCA')

In [19]:
from cplearn_v3.corespect import Corespect
corespect = Corespect(X)
corespect.extract_layers(method='stable_rank',layer_extraction_params={'q':20,'r':10,'core_fraction':0.2,'resolution':1.25})
Layers_part=corespect.layers_
c=0
for layer in Layers_part:
    c+=len(layer)
    print(len(layer),len(set(layer)))
print(c,X.shape[0])

cp1
Number of core nodes 29140
Completed with layer size:
84795 21202 23933 15774 

84795 84795
21202 21202
23933 23933
15774 15774
145704 145704


In [ ]:
from cplearn_v3.coremap import find_anchors
import importlib
importlib.reload(find_anchors)
anchor_list,anchor_dist = find_anchors.find_anchors(corespect)

In [ ]:
all_idx=[]
for ell in range(len(anchor_list)):
    for node in anchor_list[ell]:
        all_idx.append(node)

print(len(all_idx),len(Layers_part[0]),len(set(all_idx).intersection(set(Layers_part[0]))))

In [ ]:
print(len(anchor_list))
core_nodes=np.array(Layers_part[0]).astype(int)
hmap=-1*np.ones(X.shape[0])
for i,node in enumerate(core_nodes):
    hmap[node]=int(i)

c_a_labels=-1*np.ones(X.shape[0])
for ell in range(len(anchor_list)):

    print(len(anchor_list[ell]),len(set(anchor_list[ell])))

    for node in anchor_list[ell]:
        c_a_labels[node]=ell


print(X[core_nodes].shape)
print(c_a_labels.shape)


In [ ]:
partition=[[] for _ in range(len(set(label)))]
for ell in range(len(label)):
    partition[label[ell]].append(ell)

total_mat=np.zeros((len(partition),len(anchor_list)))
i1=len(partition)
j1=len(anchor_list)



for i11 in range(i1):
    for j11 in range(j1):
        total_mat[i11,j11]=len(set(partition[i11]).intersection(set(anchor_list[j11])))


In [23]:
import umap
import numpy as np
reducer=umap.UMAP()
core_nodes=np.array(Layers_part[0]).astype(int)
X_umap_c=reducer.fit_transform(X[core_nodes])
#plot_embedding(X_umap_c,labels=c_a_labels[core_nodes])


IndexError: index 65537 is out of bounds for axis 0 with size 2122

In [26]:
import umap
import numpy as np
reducer=umap.UMAP()
X_umap=reducer.fit_transform(X)
plot_embedding(X_umap,labels=label)

In [ ]:
plot_embedding(X_umap,labels=label)

In [ ]:
import os
os.environ["KMP_WARNINGS"] = "0"

In [20]:
from cplearn_v3.coremap import Coremap
cmap=Coremap(corespect)

1.25 71118 84795
Total number of clusters= 16
[13262, 11612, 11314, 8790, 6966, 6558, 5973, 5266, 5051, 3203, 1650, 1601, 1296, 1122, 566, 565]
GMM time=33.282 seconds (corrected)
Shape of embedding after round 0 is (84795, 2)
Shape of embedding after round 1 is (105997, 2)
Shape of embedding after round 2 is (129930, 2)
Shape of embedding after round 3 is (145704, 2)


In [21]:
coordinate_dict=cmap.label_dict
curr_layer=[]
for rounds,coord in enumerate(coordinate_dict):
    curr_layer.extend(Layers_part[rounds])
    print(len(curr_layer),len(set(curr_layer)))
    plot_embedding(coordinate_dict[coord],labels=label[np.array(curr_layer).astype(int)])

84795 84795


105997 105997


129930 129930


145704 145704


In [ ]:
import umap
import numpy as np
reducer=umap.UMAP()
X_umap=reducer.fit_transform(X)
plot_embedding(X_umap,labels=label)

In [ ]:
from cplearn_v3.utils.gen_utils import get_kNN
from cplearn_v3.corespect.ranking import FlowRank
from cplearn_v3.corespect.layer_extraction import find_intersection_layers
from cplearn_v3.utils.gen_utils import get_edge_list
import igraph as ig

X_stable=X[Layers_part[0]]
n1=X_stable.shape[0]
knn_list_stable,_=get_kNN(X_stable)
stable_score=FlowRank(knn_list_stable,10)
sorted_nodes= sorted(stable_score, key=lambda k: stable_score[k], reverse=True)
e_list = get_edge_list(knn_list_stable,n1)
G = ig.Graph(directed=True)
G.add_vertices(n1)
G.add_edges(e_list)
G.vs["id"] = list(range(G.vcount()))
stable_core_nodes=np.array(sorted_nodes[:int(0.25*n1)]).astype(int)
G_new=G.subgraph(stable_core_nodes)

In [ ]:
from cplearn_v3.coremap import find_anchors
import importlib
importlib.reload(find_anchors)
find_anchors.choose_stopping_res(G,stable_core_nodes)

In [ ]:
from cplearn_v3.coremap import find_anchors
import importlib
importlib.reload(find_anchors)
anchors = find_anchors.find_anchors(corespect)

In [ ]:
print(anchors)

In [ ]:
print(len(anchors))
for ell in anchors:
    print(ell.shape)

In [ ]:
plot_embedding(X_umap)

In [ ]:
import importlib
from cplearn_v3.utils import densify
importlib.reload(densify)

knn_list=corespect.knn_list

In [ ]:
G1=corespect.G
H=G1.induced_subgraph(Layers_part[0])

In [ ]:
import numpy as np
H=densify.densify_v0(np.array(knn_list).astype(int),G1,H,Layers_part[0])

In [ ]:
stable_core_nodes=np.array(sorted_nodes[:int(0.25*n1)]).astype(int)
stable_core_nodes_f = find_intersection_layers(G, stable_core_nodes, rem_nodes=np.array(stable_core_nodes).astype(int), eps=0,
                                                    mode='one_layer', res=1.25,densify=densify,adj_list=knn_list_stable)
print(len(stable_core_nodes_f),len(stable_core_nodes))

In [ ]:
import numpy as np
n=X.shape[0]
r_label=np.empty(n, dtype=object)


for i,layer in enumerate(Layers_part):
    for node in layer:
        r_label[node]= str(i+2) #str(label[node])+ str(i)


print(len(stable_core_nodes))


for node in stable_core_nodes:
    r_label[Layers_part[0][node]]= 1

for node in stable_core_nodes_f:
    r_label[Layers_part[0][node]]= 0


plot_embedding(X_umap,labels=r_label)

In [ ]:
plot_embedding(X_umap)

In [ ]:
import numpy as np
n=X.shape[0]
r_label=np.empty(n, dtype=object)
for i,layer in enumerate(Layers_part):
    for node in layer:
        r_label[node]= str(i) #str(label[node])+ str(i)

plot_embedding(X_umap,labels=r_label)

In [ ]:
import leidenalg
import numpy as np
G=corespect.G
n=G.vcount()
G_core=G.induced_subgraph(Layers_part[0])
print(G_core.vcount())
partition = leidenalg.find_partition(
    G_core,
    leidenalg.RBConfigurationVertexPartition,  # modularity-based partition
    resolution_parameter=0.7, # <-- control resolution here
    seed = np.random.randint(int(1e9))
)

# Map back to original node ids
id_map = np.array(G_core.vs["id"], dtype=int)

new_labels = -1 * np.ones(n, dtype=int)
new_labels[id_map] = partition.membership

print(len(set(new_labels)))

